In [1]:
import xlrd
import sqlite3
import time

In [2]:
# Open the workbook and define the worksheet
BOOK = xlrd.open_workbook(filename="/Users/muhamuttaqien/Desktop/Al-Qur'an/LQ Tagging/ibnKathirTafsirs DB/IndeksQuranTercanggih.xlsx")

DEPTH_TOPIC_LEVEL = 6

LIST_ENTRY = ["IMAN", "ILMU", "BANGSA-BANGSA TERDAHULU", "SEJARAH", "AL QUR'AN", 
           "AKHLAQ & ADAB", "IBADAH", "MAKANAN & MINUMAN", "PAKAIAN & PERHIASAN", 
           "HUKUM PRIVAT", "MUAMALAT", "PERADILAN & HAKIM", "HUKUM PIDANA, JINAYAH", "JIHAD"]

In [3]:
conn = sqlite3.connect("/Users/muhamuttaqien/Desktop/Al-Qur'an/LQ Tagging/IbnKathirTafsirs-tagged-parented.db3")
c = conn.cursor()

In [4]:
sheet = BOOK.sheet_by_name("IMAN")

### Count rows and columns

In [5]:
table = "tafsir_id_content"
rowsQuery = "SELECT Count() FROM %s" % table
c.execute(rowsQuery)
numberOfRows = c.fetchone()[0]
numberOfRows

6236

In [6]:
columnsQuery = "PRAGMA table_info(%s)" % table
c.execute(columnsQuery)
numberOfColumns = len(c.fetchall())
numberOfColumns

5

In [7]:
nrows = sheet.nrows
nrows

475

In [8]:
ncols = sheet.ncols
ncols

253

### Clear all keywords (optional, hit only once)

In [9]:
for row in range(numberOfRows+1):
    c.execute('UPDATE tafsir_id_content SET keywords = "" WHERE docid = ' + str(row))
    
conn.commit()

### Detect topic and verses

In [10]:
topic = sheet.cell_value(rowx=2, colx=1)
topic

'Keutamaan dan pahala iman'

In [11]:
topic = sheet.cell_value(rowx=3, colx=2)
topic

'Kesentosaan orang mukmin di dunia dan di akhirat'

In [12]:
verse = sheet.cell_value(rowx=8, colx=7)
verse

'Qs.84:8'

In [13]:
# get verses
for pcol in range(7, ncols):
    colx = pcol
    verse = sheet.cell_value(rowx=2, colx=colx).strip()
    if(verse):
        print(verse)

### Get and Update Parents

In [14]:
def get_and_update_parents(prow, pcol, depth_level, surah, ayah):
    if (depth_level > 1):
        topic_parents = []
        for up_point in range(1, depth_level):
            topic = sheet.cell_value(rowx=(prow-up_point), colx=(pcol-up_point))
            if not topic:
                
                empty_up_point = up_point
                
                while(topic == ''): # check parents if empty looped up
                    topic = sheet.cell_value(rowx=(prow-empty_up_point), colx=(pcol-up_point))
                    empty_up_point += 1
                    
                topic = topic + ' ' + str(depth_level-up_point)
                topic_parents.append(topic)
                
            else:
                topic = topic + ' ' + str(depth_level-up_point)
                topic_parents.append(topic)
        
        topic_parents_string = ', '.join(topic_parents)
                
        print("topic_parents: ", topic_parents_string)
        return topic_parents_string

### Tag topics to verses

In [ ]:
def tag_topics(entry, sheet, depth_level):
    
    nrows = sheet.nrows
    ncols = sheet.ncols
    
    for prow in range(nrows):
        pcol = depth_level # index where topics positioned
        # print("prow: ", prow)
        # print("pcol: ", pcol)
        topic = sheet.cell_value(rowx=prow, colx=pcol) # (level 1: Keutamaan dan pahala iman, Cabang-cabang iman, Hal-hal yang merusak iman)
        
        if(topic):
            print("topic: ", topic.strip())
            srow = prow+1
            
            # add hierarchy level to main topic
            topic = topic + " " + str(depth_level)
            
            for pcol_v in range(7, ncols):
                colx = pcol_v
                verse = sheet.cell_value(rowx=prow, colx=colx).strip() # (Qs.2:38, Qs.2:62, Qs.2:112)
                if(verse): 
                    # print(verse)
                    # insert verse to db
                    splitted_verse = verse[3:].split(":")
                    surah = splitted_verse[0]
                    ayah = splitted_verse[1]

                    print("Tag into Qs. "+ surah + ":"+ ayah)                      
                    
                    # set multiple tags
                    for row in c.execute('SELECT keywords FROM tafsir_id_content WHERE c0sura = '+ surah +' AND c1aya = ' + ayah):
                        if(row[0] == None or row[0] == ''):
                            topic_parents_string = get_and_update_parents(prow, pcol, depth_level, surah, ayah)
                            # print("=== Qs. "+ surah + ":"+ ayah)
                            # print("topic before: ", topic)
                            topic_verse = (topic) + (', ' + topic_parents_string)

                            # print("topic after: ", topic_verse)
                            c.execute('UPDATE tafsir_id_content SET keywords = "'+ topic_verse +'" WHERE c0sura = '+ surah +' AND c1aya = ' + ayah)
                        else:
                            topic_parents_string = get_and_update_parents(prow, pcol, depth_level, surah, ayah)
                            # print("=== Qs. "+ surah + ":"+ ayah)
                            # print("topic before: ", topic)
                            topic_verse = (topic) + (', ' + topic_parents_string)
                            joint_topic = row[0] + ", " + (topic_verse)

                            # print("joint_topic: ", joint_topic)
                            c.execute('UPDATE tafsir_id_content SET keywords = "'+ joint_topic +'" WHERE c0sura = '+ surah +' AND c1aya = ' + ayah)

    conn.commit()
    print("\n\n---------------------------------- tag %s level %s committed! ----------------------------------\n\n" % (entry, depth_level))

### Commit tagging!

#### all entries

In [18]:
start_time = time.time()

for entry in LIST_ENTRY:
    sheet = BOOK.sheet_by_name(entry)
    
    print("****************************************** %s ******************************************" % (entry))
    
    for level in range(1, (DEPTH_TOPIC_LEVEL+1)):
        tag_topics(entry, sheet, level)
    
print("--- Tagging process takes %.4f seconds ---" % (time.time() - start_time))

****************************************** IMAN ******************************************


---------------------------------- tag IMAN level 1 committed! ----------------------------------


topic_parents:  Keutamaan dan pahala iman 1
topic before:  Kesentosaan orang mukmin di dunia dan di akhirat 2
=== Qs. 2:38
topic after:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Kesentosaan orang mukmin di dunia dan di akhirat 2
=== Qs. 2:62
topic after:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Kesentosaan orang mukmin di dunia dan di akhirat 2
=== Qs. 2:112
topic after:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Kesentosaan orang mukmin di dunia dan di akhirat 2
=== Qs. 2:262
topic after:  Kesentosaan orang

topic_parents:  Keutamaan dan pahala iman 1
topic before:  Kesentosaan orang mukmin di dunia dan di akhirat 2
=== Qs. 72:13
topic after:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
=== Qs. 2:38
joint_topic:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1, Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 2:137
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 2:194
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== 

topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 9:117
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
=== Qs. 10:62
joint_topic:  Kesentosaan orang mukmin di dunia dan di akhirat 2, Keutamaan dan pahala iman 1, Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 11:41
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 11:48
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
=== Qs. 11:58
joint_topic:  Kesentosaan orang mukmin di dunia dan di 

topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 26:62
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 26:63
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 26:118
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 26:119
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 26:170
t

topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 51:35
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 52:48
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 54:13
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 54:14
topic after:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2, Keutamaan dan pahala iman 1
topic_parents:  Keutamaan dan pahala iman 1
topic before:  Orang mukmin selalu dalam lindungan Allah Ta'ala 2
=== Qs. 54:34
topi

...

topic_parents:  Pertemuan Jibril dan Nabi 5, Jibril as. 4, Beriman kepada Malaikat 3, Akidah 2, Cabang-cabang iman 1
topic before:  Pertemuan Jibril dan Nabi pada saat awal turun wahyu 6
=== Qs. 96:2
topic after:  Pertemuan Jibril dan Nabi pada saat awal turun wahyu 6, Pertemuan Jibril dan Nabi 5, Jibril as. 4, Beriman kepada Malaikat 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Pertemuan Jibril dan Nabi 5, Jibril as. 4, Beriman kepada Malaikat 3, Akidah 2, Cabang-cabang iman 1
=== Qs. 96:3
joint_topic:  Al Karim (Maha Mulia) 6, Nama-nama Allah (Asma'ul Husna) 5, Tentang nama-nama Allah 4, Beriman pada Allah Ta'ala 3, Akidah 2, Cabang-cabang iman 1, Pertemuan Jibril dan Nabi pada saat awal turun wahyu 6, Pertemuan Jibril dan Nabi 5, Jibril as. 4, Beriman kepada Malaikat 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Pertemuan Jibril dan Nabi 5, Jibril as. 4, Beriman kepada Malaikat 3, Akidah 2, Cabang-cabang iman 1
topic before:  Pertemuan Jibril dan Nabi pada saat awal turun w

topic_parents:  Timbulnya fitnah 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
=== Qs. 23:56
joint_topic:  Penangguhan (siksa) orang kafir di dunia 3, Kufur 2, Hal-hal yang merusak iman 1, Macam-macam fitnah 6, Timbulnya fitnah 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Timbulnya fitnah 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic before:  Macam-macam fitnah 6
=== Qs. 28:79
topic after:  Macam-macam fitnah 6, Timbulnya fitnah 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Timbulnya fitnah 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
=== Qs. 42:20
joint_topic:  Penangguhan (siksa) orang kafir di dunia 3, Kufur 2, Hal-hal yang merusak iman 1, Pelipatgandaan pahala bagi orang mukmin 4, Taat dan amal shaleh 3, Ketaatan dan kemaksiatan 2,

topic_parents:  Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
=== Qs. 48:29
joint_topic:  Pahala iman 2, Keutamaan dan pahala iman 1, Iman adalah ucapan dan perbuatan 2, Iman bertambah dan berkurang 1, Kekuatan umat Islam di dunia 4, Keutamaan Islam 3, Islam 2, Cabang-cabang iman 1, Keutamaan iman 4, Taat dan amal shaleh 3, Ketaatan dan kemaksiatan 2, Iman bertambah dan berkurang 1, Balasan dan pahala dari Allah 4, Taat dan amal shaleh 3, Ketaatan dan kemaksiatan 2, Iman bertambah dan berkurang 1, Ampunan Allah yang luas 5, Zat dan sifat Allah 4, Beriman pada Allah Ta'ala 3, Akidah 2, Cabang-cabang iman 1, Keutamaan umat nabi Muhammad 6, Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
=== Qs

topic_parents:  Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic before:  Abad terbaik umat Islam 6
=== Qs. 56:40
topic after:  Abad terbaik umat Islam 6, Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
topic_parents:  Perpecahan umat Islam di akhir zaman 5, Tanda-tanda kiamat kecil 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1
=== Qs. 2:206
joint_topic:  Sifat orang munafik 3, Nifak (kemunafikan) 2, Hal-hal yang merusak iman 1, Siksa orang munafik 3, Nifak (kemunafikan) 2, Hal-hal yang merusak iman 1, Ancaman bagi orang kafir dan pelaku maksiat 4, Maksiat dan dosa 3, Ketaatan dan kemaksiatan 2, Iman bertambah dan berkurang 1, Nama-nama neraka 5, Neraka 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-cabang iman 1, Sifat ahli neraka dan kejahatan mereka 5, Neraka 4, Beriman pada Hari Akhir 3, Akidah 2, Cabang-caba

TypeError: must be str, not NoneType

#### One by one

In [ ]:
LIST_ENTRY = ["IMAN", "ILMU", "BANGSA-BANGSA TERDAHULU", "SEJARAH", "AL QUR'AN", 
           "AKHLAQ & ADAB", "IBADAH", "MAKANAN & MINUMAN", "PAKAIAN & PERHIASAN", 
           "HUKUM PRIVAT", "MUAMALAT", "PERADILAN & HAKIM", "HUKUM PIDANA, JINAYAH", "JIHAD"]

start_time = time.time()
entry = "JIHAD"
sheet = BOOK.sheet_by_name(entry)

for level in range(1, (DEPTH_TOPIC_LEVEL+1)):
    tag_topics(entry, sheet, level)

print("--- Tagging process takes %.4f seconds ---" % (time.time() - start_time))